# Credit and debit card fraud detection

## Exploratory Data Analysis

## Table Of Contents: <a class="anchor" id="top"></a>

- [Introduction](#introduction)
- [Packages and the data](#packages)
- [Exploratory data analysis](#eda)
    * [Total amount purchase per month](#LineGraphic)
    * [Total count of transactions](#CountOfTransactions)
    * [Product transaction distribution](#ProductDistribution)
    * [Transactions amount boxplot](#boxplot)
    * [Cards brands distribution](#BrandsDistribution)
    * [Cards Types distribution](#BrandsTDistribution)
    * [Cards brands distribution by transaction type](#DistributionBTType)
    * [Cards distribution by transaction type](#DistributionTType)
    * [Average amount purchase](#AvgAmountPurchase)
    * [Purchase distribution by email address](#DistrByEmailAddress)
- [Conclusions](#conclusions)

### Introduction <a class="anchor" id="introduction"></a>
[TOC](#top)

Fraud can be defined as any deceitful activity that leads to obtaining unlawful advantage by one part over another or causes illegal losses. Typically, the fraudster uses false or misleading representations to disguise his/her activities as long as possible to maximize the effects of his/her fraudulent behavior. Adverse effects related to fraud have an impact on all business enterprises. The development of new technologies has also provided further ways criminals may commit fraud. Therefore, fraud detection has become essential in identifying frauds as soon as they have been committed. It is increasing substantially with the expansion of global communication technologies, resulting in considerable business losses.

The first layer of protection systems is to prevent fraud. Fraud prevention is preventing fraud from happening in the first place. This can be done by improving technologies and projects. However, the first tier is not always successful and is occasionally penetrated by fraudsters. Fraud detection is the second layer of defense, and it is responsible for detecting and recognizing fraudulent activities as they enter into systems and reporting them to a system manager.

It is impossible to be sure about the intent behind a transaction. However, fraud detection is one of the layers of general fraud control. It automates and helps reduce the manual parts of a verification process to identify a fraudulent transaction. This area has become one of the most established industrial and governmental data mining applications. Given the reality, the best cost-effective option is to discover possible evidence of fraud from the available data using automatic algorithms. Fraud detection algorithms can rely on advanced Machine Learning (ML) techniques to help fraud investigators. However, designing fraud detection algorithms is particularly challenging due to non-stationary data distributions, highly imbalanced class distributions, and continuous transaction flows.

Therefore, the purpose of this project is:
- to apply ML techniques for the fraud detection task;
- to extract performance metrics;
- to compare the use of ensemble models (Random Forests and Adaboost), decision trees and support vector machines for fraud detection;
- to use a comprehensive criterion to choose the best ML model in case of fraud detection;

### Packages and the data <a class="anchor" id="packages"></a>
[TOC](#top)

The following cell comprises all Python packages used in the project. They are necessary for visualization, scaling, sampling, feature selection, data splitting, cross-validation, classification, and performance metrics.

In [1]:
#Importing all packages necessary to implement the classification in fraud or non-fraud.
import pandas as pd
import altair as alt
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from datetime import datetime

The following cell loads the data used in the project. The Data were found in the IEEE-CIS Fraud Detection Kaggle's competition. The competition is currently closed, so I don't have access to the submissions. The data is formed by 590,540 transactions divided in 569,877 genuine transaction and 20,663 fraudulent transactions. The transactions contains money transfer and also other gifting goods and service, like you booked a ticket for others, etc.

In [2]:
#from google.colab import drive
#drive.mount('/content/drive')

In [3]:
#Importing the dataset used to train and test the machine learning models
#fraudPD = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/IEEE-CIS Fraud Detection-Transactions.csv')
fraudPD = pd.read_csv('..\CreditCardFraudDetectionData\IEEE-CIS Fraud Detection-Transactions.csv')

It is necessary to get familiar with the data user. Therefore, it is necessary to display the head of the data to have the first impression of the fields and data types.

Exploring the data's shape (number of rows and columns). The number of rows and columns seems very good for data exploration and applying ML models for classification.

In [4]:
#Let's know the shape of the data
fraudPD.shape

(590540, 394)

One central aspect of data exploration is checking the null values presented in the data. The next cell shows a short count of the null values given in the data. Despite a high amount of columns (394), the dataset has several columns full of null values. It is essential to determine how these null values will replace or drop to present this data for ML classification models.

In [5]:
#It is very important to check the amount of null values to determine how to take care of them.
fraudPD.isna().sum()

TransactionID          0
isFraud                0
TransactionDT          0
TransactionAmt         0
ProductCD              0
                   ...  
V335              508189
V336              508189
V337              508189
V338              508189
V339              508189
Length: 394, dtype: int64

### Exploratory data analysis. <a class="anchor" id="eda"></a>
[TOC](#top)

Using data visualization methods, the following exploratory data analysis (EDA) will be employed to analyze and investigate the fraud data set and summarize its main characteristics. It will help to determine how best to manipulate data sources to get the necessary answers, making it possible to discover patterns, spot anomalies, test a hypothesis, or check assumptions.
The EDA step will be used to see what data can reveal beyond the formal modeling or hypothesis testing task and provide a better understanding of data set variables and their relationships. It will also assist in determining if the statistical techniques you are considering for data analysis are appropriate.  
The primary purpose of the following EDA is to help look at data before making any assumptions. It can help identify apparent errors, better understand patterns within the data, detect outliers or abnormal events, and find exciting relations among the variables. Once this EDA is complete and insights are drawn, its features can be used for ML classification modeling.

In [6]:
#This cell changes the timestamp datetime to a readable date format.
fraudPD['time'] = fraudPD['TransactionDT'].apply(lambda x: datetime.fromtimestamp(x).strftime("%A, %B %d, %Y %I:%M:%S"))

In [7]:
#Let's separate the month to calculate the transaction amount by month.
fraudPD['month'] = pd.to_datetime(fraudPD['time']).dt.strftime('%B')
new_order = ['January', 'February', 'March', 'April', 'May', 'June', 'July'] #, 'August', 'September', 'October', 'November', 'December']
dfMonthAmount=fraudPD[['month','TransactionAmt']].groupby('month').agg('sum').reindex(new_order, axis=0).reset_index()

In [8]:
#fraudPD.to_csv('..\CreditCardFraudDetectionData\preparedFraud1.csv', encoding='utf-8', index=False)

### Total amount purchase per month <a class="anchor" id="LineGraphic"></a>
[TOC](#top)

The following graphic presents the total amount purchased month by month along the six months (from January to June) in the dataset in analysis. One can see the amount purchased in January was higher than seventeen million. The amount purchased in the following months (from February to June) is similar, with around 12 million. The dataset records just a few beginning days of purchases in July.

In [9]:
#A line chart can show the total amount values by month.
line_chart=alt.Chart(dfMonthAmount).mark_line(
    point={"filled": False, "fill": "white"}).encode(
    x=alt.X('month:N', axis=alt.Axis(labelAngle=0),
            sort=['January', 'February', 'March', 'April', 'May', 'June', 'July'],
            title='Month'),
    y=alt.Y('TransactionAmt:Q', title='Amount'))

text_chart=line_chart.mark_text(dx=0, dy=-10, align='center').encode(text=alt.Text('TransactionAmt:Q', format=',.0f'))

(line_chart + text_chart).properties(height=300, width=600, title='Total amount purchased per month')

alt.LayerChart(...)

The line chart shows the values sold in the dataset transactions for all available data (January to the beginning of July).

In [10]:
#Grouping the data in fraud and non-fraud to check the data balance.
transGroup = fraudPD[['isFraud','TransactionID']].groupby(['isFraud'], dropna=False).agg('count').reset_index()
transGroup.columns = ['isFraud','count']

### Total count of transactions <a class="anchor" id="CountOfTransactions"></a>

[TOC](#top)

One vital piece of information to visualize is the count of dataset purchases. It's a way to verify the imbalance of the data. It is one crucial aspect related to the problem of fraud detection. The fraud dataset is usually formed by a majority legitimate amount of transactions and a minority fraudulent amount of transactions. In this case, there are almost 570 thousand legitimate transactions with around 20 thousand fraudulent transactions. Transactions means purchases of products or services.

In [11]:
#Implementing a bar chart to check the data balance as fraud and non-fraud visually.
bar_chart=alt.Chart(transGroup).mark_bar().encode(
    alt.X('isFraud:N', axis=alt.Axis(labelAngle=0)),
    alt.Y('count:Q', title='Count'))
text_chart = bar_chart.mark_text(align='left', baseline='bottom', dx=-5).encode(text='count:Q')
(bar_chart + text_chart).properties(height=300, width=400, title='Total count of transactions')

alt.LayerChart(...)

The data is very unbalanced, and it must be balanced before presenting it to a machine-learning model.

Grouping by product code, the product for each transaction. Product isn't necessary to be a real 'product' (like one item to be added to the shopping cart). It could be any kind of service.

In [12]:
productCDGroup = fraudPD[['ProductCD','TransactionID']].groupby(['ProductCD'], dropna=False).agg('count').reset_index()
productCDGroup.columns = ['ProductCD','count']

### Product transaction distribution <a class="anchor" id="ProductDistribution"></a>

[TOC](#top)

Another exciting piece of information is about the count of products purchased. The dataset has just five products purchased. According to the information in the Kaggle, this field stores some product codes (C, H, R, S, and W). Those are the products of each transaction. The product doesn't necessarily have to be genuine (like one item to be added to the shopping cart). It could be any service. One can verify that product code W has the highest number of purchases, with almost 440 thousand. The other four products have lower than 70 thousand counts purchased.

In [13]:
bar_chart=alt.Chart(productCDGroup).mark_bar().encode(
    alt.X('ProductCD:N', axis=alt.Axis(labelAngle=0), title='Product or service'),
    alt.Y('count:Q', title='Count'))
text_chart = bar_chart.mark_text(align='left', baseline='bottom', dx=-15).encode(text='count:Q')
(bar_chart + text_chart).properties(height=300, width=400, title='Product or service transactions distribution')

alt.LayerChart(...)

### Transactions amount boxplot <a class="anchor" id="boxplot"></a>

[TOC](#top)

In [14]:
Q1 = fraudPD['TransactionAmt'].quantile(0.25)
Q3 = fraudPD['TransactionAmt'].quantile(0.75)
IQR = Q3 - Q1    #IQR is interquartile range.

filter = (fraudPD['TransactionAmt'] >= Q1 - 1.5 * IQR) & (fraudPD['TransactionAmt'] <= Q3 + 1.5 *IQR)
filterFraudOutliers=fraudPD.loc[filter]

In [15]:
alt.Chart(filterFraudOutliers.sample(1000)).mark_boxplot(size=50).encode(
    alt.X("ProductCD:N", axis=alt.Axis(labelAngle=0), title='Product or service'),
    alt.Y("TransactionAmt:Q", title='Amount purchased'),
    alt.Color("ProductCD:N", legend=None),
).properties(width=500, height=300, title="Products and services boxplot")

alt.Chart(...)

The bar chart illustrates the dataset distribution of product types.

In [16]:
#Grouping the data according to the card types.
card4Group = fraudPD[['card4','TransactionID']].groupby(['card4'], dropna=False).agg('count').reset_index()
card4Group.columns = ['card4','count']

### Cards brands distribution <a class="anchor" id="BrandsDistribution"></a>

[TOC](#top)

One can see how the data is distributed regarding the card brands. The dataset has four brands: American Express, Discover, Mastercard and Visa. It is possible to verify the Visa brand's dominance of purchases, with almost 400 thousand purchases. The Mastercard brand follows it with nearly 190 thousand purchases. American Express has around 8 thousand purchases, and Discover has over 6 thousand.

In [17]:
#The bar chart presents the amount of each credit card brand used in the transactions.
bar_chart=alt.Chart(card4Group).mark_bar(size=40).encode(
    x=alt.X('count:Q', title='Count'),
    y=alt.Y('card4:N', title='Card brands'))
bar_text = bar_chart.mark_text(align='left', baseline='middle', dx=5).encode(text='count:Q')
(bar_chart + bar_text).properties(height=alt.Step(50), width=600, title='Cards brands transactions distribution')

alt.LayerChart(...)

In [18]:
#Grouping and counting the transactions according to credit card types.
card6Group = fraudPD[['card6','TransactionID']].groupby(['card6'], dropna=False).agg('count').reset_index()
card6Group.columns = ['card6','count']

### Cards Types distribution <a class="anchor" id="BrandsTDistribution"></a>

[TOC](#top)

There are two main ways to purchase using a card: debit or credit. The dataset has a third way called charge, but it has just 15 purchases in total. Debit cards have the highest number of purchases, with almost 440 thousand. It is followed by credit cards with nearly 150 thousand purchases. This information is fascinating because it shows the domain of debit purchases instead of credit purchases.

In [19]:
#Visually presenting the amount of transactions according to credit card type.
bar_chart=alt.Chart(card6Group).mark_bar(size=40).encode(
    x=alt.X('count:Q', title='Count'),
    y=alt.Y('card6:N', title='Card type'))
bar_text = bar_chart.mark_text(align='left', baseline='middle', dx=5).encode(text='count:Q')
(bar_chart + bar_text).properties(height=alt.Step(50), width=600, title='Card types distribution')

alt.LayerChart(...)

In [20]:
#Grouping the transactions by credit brand and transaction type (genuine or fraudulent).
card4Group = fraudPD[['card4','TransactionID','isFraud']].groupby(['card4','isFraud'], dropna=False).agg('count').reset_index()
card4Group.columns = ['card4','isFraud','count']

### Cards brands distribution by transaction type <a class="anchor" id="DistributionBTType"></a>

[TOC](#top)

One can verify the count of brand purchases by considering the type of transaction (legitimate-0 or fraudulent-1). The Visa card is the most used, with over 370 thousand legitimate 13 thousand fraudulent transactions. Mastercard follows it with around 180 thousand transactions and almost 6500 fraudulent transactions. It is possible to conclude that the number of fraudulent transactions is unrelated to a specific card brand because the amount of fraudulent transactions is around 3.5% for both Visa and Mastercard.

In [21]:
#Let's visually check the number of credit-type transactions that are fraudulent or genuine.
bar_chart = alt.Chart(card4Group).encode(
    alt.X("isFraud:O", axis=alt.Axis(labelAngle=0)),
    alt.Y("sum(count):Q", title='Count'),
    alt.Color("isFraud:N"),
    alt.Text("sum(count):Q", format=".0f"),
).properties(height=alt.Step(50), width=100)

alt.layer(
    bar_chart.mark_bar(size=40),
    bar_chart.mark_text(dy=-10)
).facet(
    alt.Column("card4:N", title='Cards brands transactions distribution by transaction type')
).configure_facet(spacing=0)


alt.FacetChart(...)

In [22]:
#Let's group the transactions by card type (credit or debit) divided by fraudulent or legitimate transactions.
card6Group = fraudPD[['card6','TransactionID','isFraud']].groupby(['card6','isFraud'], dropna=False).agg('count').reset_index()
card6Group.columns = ['card6','isFraud','count']

### Cards distribution by transaction type <a class="anchor" id="DistributionTType"></a>

[TOC](#top)

The following graphic presents the number of transactions (purchases) by credit card divided into legitimate-0 transactions and fraudulent-1 transactions. One can verify the domain of debit card transactions with almost 430 thousand legitimate transactions and over 10 thousand fraudulent transactions. It is followed by credit card transactions with practically 140 thousand legitimate transactions and nearly 10 thousand transactions. One can have an essential insight with this graphic: It is possible to verify that 7.15% of credit card transactions are fraudulent while only 2.5% of debit transactions are fraudulent. Fraudsters use three times more credit cards than debit cards.

In [23]:
#One can see the distribution of transactions by card and type of transactions.
bar_chart = alt.Chart(card6Group).encode(
    alt.X("isFraud:O", axis=alt.Axis(labelAngle=0)),
    alt.Y("sum(count):Q", title='Count'),
    alt.Color("isFraud:N"),
    alt.Text("sum(count):Q", format=".0f"),
).properties(height=alt.Step(50), width=100)

alt.layer(
    bar_chart.mark_bar(size=40),
    bar_chart.mark_text(dy=-10)
).facet(
    alt.Column("card6:N", title='Cards transactions distribution by transaction type')
).configure_facet(spacing=0)

alt.FacetChart(...)

In [24]:
#One exciting piece of information compares the purchase profiles of legitimate and fraudulent transactions.
#Let's calculate the average purchase amounts by legitimate and fraudulent transactions.
tAmountdf = fraudPD[['isFraud','TransactionAmt']].groupby('isFraud').mean().reset_index()

### Average amount purchase <a class="anchor" id="AvgAmountPurchase"></a>

[TOC](#top)

The graphic shows that the average purchase amounts for fraudulent and legitimate transactions are similar. On average, 135 dollars are for legitimate transactions and 149 for fraudulent transactions. One intriguing insight with this graphic is that fraudsters usually try to simulate legitimate transactions to avoid fraudulent transaction prevention systems.

In [25]:
#One can check the purchase amount average for each kind of transaction.
pie_chart=alt.Chart(tAmountdf).mark_arc(outerRadius=150).encode(
    theta=alt.Theta("TransactionAmt:Q", stack=True),
    color=alt.Color("isFraud:N"))

bar_text = pie_chart.mark_text(radius=165, size=15,fill= "black").encode(text=alt.X('TransactionAmt:Q', format=".0f"))

(pie_chart + bar_text).properties(title='Average amount purchased')

alt.LayerChart(...)

In [26]:
#Let's unpivot a wide to long format fraud data frame to have P_emaildomain and R_emaildomain as columns.
fraudMelt=pd.melt(fraudPD[['TransactionID','P_emaildomain','R_emaildomain']],
                  id_vars=['TransactionID'],
               value_vars=['P_emaildomain', 'R_emaildomain'], ignore_index=False)

#So, one can count how many domains are present in the transactions.
fraudMelt=fraudMelt[['variable','value']].value_counts().reset_index()
fraudMelt.columns = ['address','domain','count']

#Then, one can count how many transactions for the first five domain addresses.
fraudGrp = fraudMelt[['domain','count']].groupby('domain').sum().sort_values('count', ascending=False).head(5)
fraudMelt=fraudMelt.merge(fraudGrp, how='inner', on='domain')[['address','domain','count_x']]
fraudMelt.columns = ['address','domain','count']

### Purchase distribution by email address <a class="anchor" id="DistrByEmailAddress"></a>

[TOC](#top)

Most purchases and recipients have an email domain. Therefore, verifying how such domains distribute the number of transactions is insightful. The following graphic presents the distribution of email domains for purchasers and recipients. One can see that the primary email domain used is gmail.com, with almost 230 thousand transactions to purchase a domain and nearly 60 thousand transactions for the recipient domain, followed by yahoo.com and hotmail.com. Certain transactions don't need a recipient, so such domains are null.

In [27]:
#Let's see the graphic of the email domain address distribution for purchasers and recipients
bar_chart = alt.Chart(fraudMelt).encode(
    alt.X("address:O", axis=alt.Axis(labelAngle=45)),
    alt.Y("count:Q", title='Count'),
    alt.Color("address:N"),
    alt.Text("count:Q", format=".0f"),
).properties(height=alt.Step(50), width=100)

alt.layer(
    bar_chart.mark_bar(size=40),
    bar_chart.mark_text(dy=-10)
).facet(
    alt.Column("domain:N", title='Purshase distribution by email address')
).configure_facet(spacing=0)

alt.FacetChart(...)

## Conclusions <a class="anchor" id="conclusions"></a>

[TOC](#top)

The data was investigated by checking for data unbalancing, visualizing the features, checking the null values, and understanding the relationship between different features. The data were split into train and test sets and scaled, and a feature selection technique based on feature importance was employed and evaluated for use in further pipelines. The hyperparameters were prepared for optimization, and a pipeline was created for each model with feature selection, scaling, hyperparameters tunning, and classification steps. The performance of Decision Trees, Random Forests, and Support Vector Machines are very similar. However, Adaboost ensemble machine learning models present the general best performance compared to all analyzed models. Another work that will be completed in the future is using neural nets to see if we could further improve the model results.